# Advanced Topics in Stochastic Modelling - Mini Project
- Chirag Shivakumar 1004996
- Tze Liang 1005452

# Project Name - Use of regenerative simulation method for staffing call centers

## Project Objective
Minimize the number of call center agents while ensuring service quality metrics are met
- less than 2% abandonment and
- average wait time under five seconds


The project involves using a regenerative simulation method to determine the optimal staffing level in a call center to meet specified performance constraints with 95% confidence.

In [1]:
import numpy as np
import pandas as pd
import plotly.graph_objects as go
from scipy.stats import uniform, norm, t
import plotly.express as px

# Part A

## Define Parameters and Constraints

In [2]:
HOURS_OPEN = 8
SECONDS_OPEN = HOURS_OPEN * 3600
ARRIVALS_PER_MINUTE = 20
MEAN_SERVICE_TIME = 3 * 60

LAMBDA = ARRIVALS_PER_MINUTE / 60
MU = 1 / MEAN_SERVICE_TIME

MAX_WAIT_TIME = 5
MAX_ABANDONMENT_RATE = 0.02

MIN_PATIENCE_TIME = 0
MAX_PATIENCE_TIME = 6 * 60

# Constants for the 95% confidence interval
CONFIDENCE_LEVEL = 0.95
Z_SCORE = norm.ppf((1 + CONFIDENCE_LEVEL) / 2)  # Z-score for 95% confidence

## Run Simulation with 95% Confidence Interval

In [3]:
# Updated simulation function with confidence intervals
def simulate_call_center_with_confidence(num_agents, num_calls, seed=42):
    np.random.seed(seed)
    # Generate call arrivals and service times
    arrival_times = np.cumsum(np.random.exponential(scale=1/LAMBDA, size=num_calls))
    service_times = np.random.exponential(scale=MEAN_SERVICE_TIME, size=num_calls)
    patience_times = uniform(loc=MIN_PATIENCE_TIME, scale=MAX_PATIENCE_TIME).rvs(size=num_calls)

    agents = np.zeros(num_agents)
    wait_times = []
    abandonments = 0

    for i in range(num_calls):
        if arrival_times[i] > SECONDS_OPEN:
            continue
        available_agent = np.where(agents <= arrival_times[i])[0]
        if available_agent.size > 0:
            agent_index = available_agent[0]
            agents[agent_index] = arrival_times[i] + service_times[i]
            wait_times.append(0)
        else:
            next_available_time = np.min(agents)
            wait_time = next_available_time - arrival_times[i]
            if wait_time > patience_times[i]:
                abandonments += 1
            else:
                agent_index = np.argmin(agents)
                agents[agent_index] = next_available_time + service_times[i]
                wait_times.append(wait_time)

    average_wait_time = np.mean(wait_times) if wait_times else 0
    abandonment_rate = abandonments / num_calls if num_calls else 0

    # Calculate confidence intervals
    wait_time_std = np.std(wait_times) if wait_times else 0
    wait_time_ci = Z_SCORE * wait_time_std / np.sqrt(len(wait_times)) if wait_times else 0

    abandonment_rate_ci = Z_SCORE * np.sqrt(abandonment_rate * (1 - abandonment_rate) / num_calls) if num_calls else 0

    return {
        'num_agents': num_agents,
        'average_wait_time': average_wait_time,
        'wait_time_ci': wait_time_ci,
        'abandonment_rate': abandonment_rate,
        'abandonment_rate_ci': abandonment_rate_ci,
        'abandonments': abandonments,
        'total_calls': num_calls
    }

### Plot Simulation

In [4]:
arrival_times = np.cumsum(np.random.exponential(scale=1/LAMBDA, size=int(ARRIVALS_PER_MINUTE * 60 * HOURS_OPEN)))

# Assuming calls are answered instantly, call end times are just the arrival times plus service time
call_end_times = arrival_times + MEAN_SERVICE_TIME

# Time points to evaluate the number of calls in progress
time_points = np.arange(0, SECONDS_OPEN + 1, 1)
num_calls_in_progress_a = np.zeros_like(time_points)

# Count the number of calls in progress at each time point
for i, time_point in enumerate(time_points):
    num_calls_in_progress_a[i] = np.sum((arrival_times <= time_point) & (call_end_times > time_point))

# Plotting
fig = go.Figure(data=[
    go.Scatter(x=time_points, y=num_calls_in_progress_a, mode='lines', name='Calls in Progress')
])

# Update the layout
fig.update_layout(
    title="Number of Calls in Progress Over Time",
    xaxis_title="Time (seconds)",
    yaxis_title="Number of Calls in Progress",
    xaxis=dict(range=[0, SECONDS_OPEN]),
    yaxis=dict(range=[0, num_calls_in_progress_a.max() + 1])
)

# Show the figure
fig.show()

## Find the Optimal Staffing 

In [5]:
# Updated function to find the optimal staffing level with confidence intervals
def find_optimal_staffing_with_confidence():
    num_calls = int(ARRIVALS_PER_MINUTE * 60 * HOURS_OPEN)
    num_agents = int(np.ceil(LAMBDA * SECONDS_OPEN / MEAN_SERVICE_TIME))
    optimal_found = False
    results = []

    while not optimal_found:
        simulation_result = simulate_call_center_with_confidence(num_agents, num_calls)
        results.append(simulation_result)

        avg_wait_time = simulation_result['average_wait_time']
        wait_time_ci = simulation_result['wait_time_ci']
        abandonment_rate = simulation_result['abandonment_rate']
        abandonment_rate_ci = simulation_result['abandonment_rate_ci']

        # Check if the performance metrics are within limits, including their confidence intervals
        if avg_wait_time - wait_time_ci <= MAX_WAIT_TIME and abandonment_rate + abandonment_rate_ci <= MAX_ABANDONMENT_RATE:
            optimal_found = True
        else:
            num_agents += 1

    return num_agents, pd.DataFrame(results)

optimal_agents_with_confidence, simulation_results_with_confidence = find_optimal_staffing_with_confidence()

### Optimal Number of Staff

In [6]:
optimal_agents_with_confidence

67

### Dataframe with Analysis

In [7]:
simulation_results_with_confidence

num_agents  average_wait_time  wait_time_ci  abandonment_rate  \
0           54          44.838363      0.594034          0.130625   
1           55          39.287063      0.573316          0.115000   
2           56          34.162803      0.544935          0.099583   
3           57          29.411451      0.518772          0.087083   
4           58          24.889481      0.481529          0.075000   
5           59          21.125166      0.447519          0.064583   
6           60          17.639843      0.405450          0.052604   
7           61          14.488439      0.374112          0.044375   
8           62          11.872634      0.340531          0.036771   
9           63          10.051799      0.312827          0.030312   
10          64           8.056772      0.281572          0.025104   
11          65           6.744034      0.255567          0.019896   
12          66           5.237669      0.222313          0.016354   
13          67           4.159098      0.193319          0.013125   

    abandonment_rate_ci  abandonments  total_calls  
0              0.006741          1254         9600  
1              0.006382          1104         9600  
2              0.005990           956         9600  
3              0.005640           836         9600  
4              0.005269           720         9600  
5              0.004917           620         9600  
6              0.004466           505         9600  
7              0.004119           426         9600  
8              0.003765           353         9600  
9              0.003430           291         9600  
10             0.003129           241         9600  
11             0.002793           191         9600  
12             0.002537           157         9600  
13             0.002277           126         9600

In [8]:
import plotly.graph_objects as go

def plot_simulation_results(simulation_results_df):
    # Initialize figure
    fig = go.Figure()

    # Add a scatter plot for average wait times
    fig.add_trace(go.Scatter(
        x=simulation_results_df['num_agents'], 
        y=simulation_results_df['average_wait_time'], 
        mode='lines+markers', 
        name='Average Wait Time (seconds)'
    ))

    # Add a scatter plot for abandonment rates
    fig.add_trace(go.Scatter(
        x=simulation_results_df['num_agents'], 
        y=simulation_results_df['abandonment_rate'], 
        mode='lines+markers', 
        name='Abandonment Rate',
        yaxis='y2'  # Assign to the secondary y-axis
    ))

    # Edit the layout
    fig.update_layout(
        title='Average Wait Time and Abandonment Rate vs. Number of Agents',
        xaxis_title='Number of Agents',
        yaxis_title='Average Wait Time (seconds)',
        yaxis2=dict(
            title='Abandonment Rate',
            overlaying='y',
            side='right',
            tickformat='.1%'
        ),
        legend=dict(
            x=0.7,
            y=0.95,
            traceorder='reversed',
            title_font_family='Arial',
            font=dict(
                family='Arial',
                size=12,
                color='black'
            ),
            bgcolor='LightSteelBlue',
            bordercolor='Black',
            borderwidth=2
        )
    )

    # Show plot
    fig.show()

# Now you would call this function with the simulation results DataFrame
plot_simulation_results(simulation_results_with_confidence)

## Verify that the Average Waiting Time and the Abandonment Rate Match. Use Regenerative Simulation as taught in Class

### Verify Average Waiting Time

#### Simulation 

In [9]:
# Adjusting the simulation function to record individual wait times and abandonment times
def simulate_call_center_with_detailed_data(num_agents, num_calls, seed=42):
    np.random.seed(seed)
    arrival_times = np.cumsum(np.random.exponential(scale=1/LAMBDA, size=num_calls))
    service_times = np.random.exponential(scale=MEAN_SERVICE_TIME, size=num_calls)
    patience_times = uniform(loc=MIN_PATIENCE_TIME, scale=MAX_PATIENCE_TIME).rvs(size=num_calls)

    agents = np.zeros(num_agents)
    detailed_wait_times = []  # Store individual wait times
    detailed_abandonment_times = []  # Store individual abandonment times

    for i in range(num_calls):
        if arrival_times[i] > SECONDS_OPEN:
            continue
        available_agent = np.where(agents <= arrival_times[i])[0]
        if available_agent.size > 0:
            agent_index = available_agent[0]
            agents[agent_index] = arrival_times[i] + service_times[i]
            detailed_wait_times.append(0)
        else:
            next_available_time = np.min(agents)
            wait_time = next_available_time - arrival_times[i]
            if wait_time > patience_times[i]:
                detailed_abandonment_times.append(arrival_times[i] + wait_time)
            else:
                agent_index = np.argmin(agents)
                agents[agent_index] = next_available_time + service_times[i]
                detailed_wait_times.append(wait_time)

    return detailed_wait_times, detailed_abandonment_times

num_calls = int(ARRIVALS_PER_MINUTE * 60 * HOURS_OPEN)
# optimal_agents_with_confidence = 66 # delete later
detailed_wait_times, detailed_abandonment_times = simulate_call_center_with_detailed_data(optimal_agents_with_confidence, num_calls)

#### Create Dataframe

In [10]:
# Creating the wait times dataset
wait_times_df = pd.DataFrame({'wait_time': detailed_wait_times})
wait_times_df['call_number'] = wait_times_df.index + 1  # Call numbers start from 1

wait_times_df

wait_time  call_number
0      0.000000            1
1      0.000000            2
2      0.000000            3
3      0.000000            4
4      0.000000            5
...         ...          ...
9469  11.685354         9470
9470  13.362176         9471
9471  17.312146         9472
9472  16.581938         9473
9473  17.159164         9474

[9474 rows x 2 columns]

#### Plot Waiting Time (Y-axis) vs No. of Calls (X-axis)

In [11]:
# Plotting the wait times graph similar to the queueing system example
fig = px.line(wait_times_df, x='call_number', y='wait_time',
             labels={'call_number': 'Call Number', 'wait_time': 'Wait Time'},
             title='Wait Times per Call Number')

fig.update_layout(barmode='overlay', bargap=0)
fig.show()

#### Regenrative Simulation Process

In [12]:
# Using the wait_times_df dataframe to identify cycles, cycle lengths, and rewards
# Assuming that a 'cycle' in the context of the call center is a period where wait times are continuously non-zero

# Adding a column to indicate whether the call had a wait time or not
wait_times_df['had_wait'] = wait_times_df['wait_time'] > 0

# Identifying the start of cycles
wait_times_df['cycle_start'] = wait_times_df['had_wait'] & ~wait_times_df['had_wait'].shift(1).fillna(False)

# Assigning cycle numbers
wait_times_df['cycle_number'] = wait_times_df['cycle_start'].cumsum()

# Calculating cycle lengths and rewards
cycle_info = wait_times_df.groupby('cycle_number').agg(
    cycle_length=('call_number', 'count'),  # Count of calls in the cycle
    Reward=('wait_time', 'sum')  # Sum of wait times in the cycle
).reset_index()

cycle_info  # Displaying the first few rows

cycle_number  cycle_length      Reward
0               0           353    0.000000
1               1            21   85.275340
2               2           270   21.973600
3               3             2    0.556745
4               4             5    5.827596
..            ...           ...         ...
192           192             7    7.159722
193           193             5   11.873690
194           194            17   21.295967
195           195           187  141.133003
196           196             7   86.926157

[197 rows x 3 columns]

##### Step 0: Choose the number of cycles (denoted by $ N $) to simulate

In [13]:
N = cycle_info.shape[0]  # The total number of cycles

##### Step 1: Identify regeneration times $ S_0, S_1, \ldots, S_N $ from simulation


##### Step 2: Compute reward for each cycle - Reward in $ n^{th} $ cycle 


##### Step 3: Compute average cycle length, $ \bar{C} = \frac{1}{N} \sum_{n=1}^N C_n $, where $ C_n = S_n - S_{n-1} $ and average reward over cycles, $ \bar{R} = \frac{1}{N} \sum_{n=1}^N R_n $

In [14]:
# Step 3: Compute average cycle length and average reward over cycles
N = cycle_info.shape[0]  # The total number of cycles
average_cycle_length = cycle_info['cycle_length'].mean()
average_reward = cycle_info['Reward'].mean()

##### Step 4: Output $ \frac{\bar{R}}{\bar{C}} $ as an estimate for as the steady-state average


In [15]:
# Output the average reward over cycles divided by average cycle length
average_reward_per_cycle_length = average_reward / average_cycle_length

##### Step 5: To compute a confidence interval, compute sample variances and covariances as below:

$$ s_{11}^2 = \frac{1}{N - 1} \sum_{i=1}^N (R_i - \bar{R})^2 $$

$$ s_{22}^2 = \frac{1}{N - 1} \sum_{i=1}^N (C_i - \bar{C})^2 $$

$$ s_{12} = \frac{1}{N - 1} \sum_{i=1}^N (R_i - \bar{R})(C_i - \bar{C}) $$

Then take,

$$ s^2 = s_{11}^2 - 2 \frac{\bar{R}}{\bar{C}} s_{12} + \left(\frac{\bar{R}}{\bar{C}}\right)^2 s_{22}^2 $$

In [16]:
# Step 5: Compute sample variances and covariances
s11_squared = ((cycle_info['Reward'] - average_reward) ** 2).sum() / (N - 1)
s22_squared = ((cycle_info['cycle_length'] - average_cycle_length) ** 2).sum() / (N - 1)
s12 = ((cycle_info['Reward'] - average_reward) * (cycle_info['cycle_length'] - average_cycle_length)).sum() / (N - 1)

##### Step 6: Output the $ (1 - \alpha) \times 100\% $ as:

$$ \left( \frac{\bar{R}}{\bar{C}} + \frac{{s}z_{\alpha/2}}{\bar{C}\sqrt{N}}, \frac{\bar{R}}{\bar{C}} - \frac{{s}z_{\alpha/2}}{\bar{C}\sqrt{N}} \right) $$

In [17]:
# The variance of the estimator
s_squared = s11_squared - 2 * (average_reward / average_cycle_length) * s12 + ((average_reward / average_cycle_length) ** 2) * s22_squared

# Step 6: Output the 95% confidence interval for the steady-state average
alpha = 0.05  # for a 95% confidence interval
z_alpha_over_2 = t.ppf(1 - alpha/2, df=N-1)  # t-score for 95% CI and N-1 degrees of freedom
margin_of_error = z_alpha_over_2 / (average_cycle_length * (N** 0.5) )

lower_bound = average_reward_per_cycle_length - margin_of_error
upper_bound = average_reward_per_cycle_length + margin_of_error

##### Verified Answer 

In [18]:
print(average_reward_per_cycle_length)
print(lower_bound)
print(upper_bound)

4.159098260724547
4.156176546442517
4.162019975006577


### Verify Abandon Rate 

#### Simulation 

In [19]:
# Adjusting the function to track detailed wait times and abandonment times accurately

def simulate_call_center_with_detailed_data(num_agents, num_calls, seed=42):
    np.random.seed(seed)
    arrival_times = np.cumsum(np.random.exponential(scale=1/LAMBDA, size=num_calls))
    service_times = np.random.exponential(scale=MEAN_SERVICE_TIME, size=num_calls)
    patience_times = uniform(loc=MIN_PATIENCE_TIME, scale=MAX_PATIENCE_TIME).rvs(size=num_calls)

    agents = np.zeros(num_agents)
    detailed_wait_times = []  # Store individual wait times
    detailed_abandonment_times = []  # Store individual abandonment times

    for i in range(num_calls):
        if arrival_times[i] > SECONDS_OPEN:
            continue
        available_agent = np.where(agents <= arrival_times[i])[0]
        if available_agent.size > 0:
            agent_index = available_agent[0]
            agents[agent_index] = arrival_times[i] + service_times[i]
            detailed_wait_times.append(0)
        else:
            next_available_time = np.min(agents)
            wait_time = next_available_time - arrival_times[i]
            if wait_time > patience_times[i]:
                detailed_abandonment_times.append(arrival_times[i] + wait_time)
            else:
                agent_index = np.argmin(agents)
                agents[agent_index] = next_available_time + service_times[i]
                detailed_wait_times.append(wait_time)

    return detailed_wait_times, detailed_abandonment_times

# Running the simulation again
optimal_agents = optimal_agents_with_confidence
num_calls = int(ARRIVALS_PER_MINUTE * 60 * HOURS_OPEN)
_, detailed_abandonment_times = simulate_call_center_with_detailed_data(optimal_agents, num_calls)

#### Create Dataframe

In [20]:
# Rounding abandonment times to the nearest integer and creating the initial abandonment dataframe
abandonment_df_initial = pd.DataFrame(np.round(detailed_abandonment_times), columns=['second'])
abandonment_df_initial['abandoned_calls'] = 1
abandonment_df_initial = abandonment_df_initial.groupby('second').sum().reset_index()

# Creating a complete dataframe including all seconds in the 8-hour period
all_seconds = np.arange(0, SECONDS_OPEN + 1, 1)
abandonment_df = pd.DataFrame(all_seconds, columns=['second'])
abandonment_df = abandonment_df.merge(abandonment_df_initial, on='second', how='left')
abandonment_df['abandoned_calls'].fillna(0, inplace=True)

abandonment_df.head()  # Displaying the first few rows of the complete dataframe

second  abandoned_calls
0       0              0.0
1       1              0.0
2       2              0.0
3       3              0.0
4       4              0.0

#### Plot Abandoned Calls (Y-axis) vs Seconds (X-axis)

In [21]:
# Now we plot the bar graph for abandoned calls per second using Plotly Express
abandonment_fig = px.line(abandonment_df, x='second', y='abandoned_calls',
                         labels={'second': 'Second', 'abandoned_calls': 'Abandoned Calls'},
                         title='Abandoned Calls per Second')


abandonment_fig.show()

#### Regenrative Simulation Process

In [22]:
# Identifying cycles of abandoned calls, similar to wait times analysis
# A 'cycle' in this context will be a period where abandoned calls are continuously non-zero

# Adding a column to indicate whether there was an abandoned call or not
abandonment_df['had_abandonment'] = abandonment_df['abandoned_calls'] > 0

# Identifying the start of cycles
abandonment_df['cycle_start'] = abandonment_df['had_abandonment'] & ~abandonment_df['had_abandonment'].shift(1).fillna(False)

# Assigning cycle numbers
abandonment_df['cycle_number'] = abandonment_df['cycle_start'].cumsum()

# Calculating cycle lengths and rewards (in this case, the reward is the number of abandoned calls)
abandonment_cycle_info = abandonment_df.groupby('cycle_number').agg(
    cycle_length=('second', 'count'),  # Count of seconds in the cycle
    Reward=('abandoned_calls', 'sum')  # Sum of abandoned calls in the cycle
).reset_index()


abandonment_cycle_info

cycle_number  cycle_length  Reward
0               0          1983     0.0
1               1           673     1.0
2               2            10     1.0
3               3            36     1.0
4               4           175     1.0
..            ...           ...     ...
108           108           173     2.0
109           109            16     1.0
110           110           188     1.0
111           111           524     1.0
112           112           624     1.0

[113 rows x 3 columns]

##### Step 0: Choose the number of cycles (denoted by $ N $) to simulate

In [23]:
N = cycle_info.shape[0]  # The total number of cycles

##### Step 1: Identify regeneration times $ S_0, S_1, \ldots, S_N $ from simulation

##### Step 2: Compute reward for each cycle - Reward in $ n^{th} $ cycle 

##### Step 3: Compute average cycle length, $ \bar{C} = \frac{1}{N} \sum_{n=1}^N C_n $, where $ C_n = S_n - S_{n-1} $ and average reward over cycles, $ \bar{R} = \frac{1}{N} \sum_{n=1}^N R_n $

In [24]:
average_cycle_length = (abandonment_cycle_info['cycle_length'].mean())
average_cycle_length = (average_cycle_length*9600)/(8*60*60) # TAKE NOTE 
average_reward = abandonment_cycle_info['Reward'].mean()

##### Step 4: Output $ \frac{\bar{R}}{\bar{C}} $ as an estimate for as the steady-state average

In [25]:
# Output the average reward over cycles divided by average cycle length
average_reward_per_cycle_length = average_reward / average_cycle_length

##### Step 5: To compute a confidence interval, compute sample variances and covariances as below:

$$ s_{11}^2 = \frac{1}{N - 1} \sum_{i=1}^N (R_i - \bar{R})^2 $$

$$ s_{22}^2 = \frac{1}{N - 1} \sum_{i=1}^N (C_i - \bar{C})^2 $$

$$ s_{12} = \frac{1}{N - 1} \sum_{i=1}^N (R_i - \bar{R})(C_i - \bar{C}) $$

Then take,

$$ s^2 = s_{11}^2 - 2 \frac{\bar{R}}{\bar{C}} s_{12} + \left(\frac{\bar{R}}{\bar{C}}\right)^2 s_{22}^2 $$

In [26]:
s11_squared = ((abandonment_cycle_info['Reward'] - average_reward) ** 2).sum() / (N - 1)
s22_squared = ((abandonment_cycle_info['cycle_length'] - average_cycle_length) ** 2).sum() / (N - 1)
s12 = ((abandonment_cycle_info['Reward'] - average_reward) * (abandonment_cycle_info['cycle_length'] - average_cycle_length)).sum() / (N - 1)

s_squared = s11_squared - 2 * (average_reward / average_cycle_length) * s12 + ((average_reward / average_cycle_length) ** 2) * s22_squared

##### Step 6: Output the $ (1 - \alpha) \times 100\% $ as:

$$ \left( \frac{\bar{R}}{\bar{C}} - s\frac{z_{\alpha/2}}{\sqrt{N}}, \frac{\bar{R}}{\bar{C}} + s\frac{z_{\alpha/2}}{\sqrt{N}} \right) $$

In [27]:
# Step 6: Output the 95% confidence interval for the steady-state average
alpha = 0.05  # for a 95% confidence interval
z_alpha_over_2 = t.ppf(1 - alpha/2, df=N-1)  # t-score for 95% CI and N-1 degrees of freedom
margin_of_error = z_alpha_over_2 / (average_cycle_length * (N** 0.5) )


lower_bound = average_reward_per_cycle_length - margin_of_error
upper_bound = average_reward_per_cycle_length + margin_of_error

##### Verified Output

In [28]:
print(average_reward_per_cycle_length)
print(lower_bound)
print(upper_bound)

0.013124544286656712
0.011470690816820724
0.0147783977564927


# Part B

## Define Parameters and Constraints

In [29]:
HOURS_OPEN = 8
SECONDS_OPEN = HOURS_OPEN * 3600
ARRIVALS_PER_MINUTE = 20
MEAN_SERVICE_TIME = 3 * 60
LAMBDA = ARRIVALS_PER_MINUTE / 60
MU = 1 / MEAN_SERVICE_TIME
MAX_WAIT_TIME = 5
MAX_ABANDONMENT_RATE = 0.02
MIN_PATIENCE_TIME = 0
MAX_PATIENCE_TIME_1 = 1 * 60  # mean = 1 minute for impatient callers
MAX_PATIENCE_TIME_2 = 5 * 60  # mean = 5 minutes for patient callers
PROBABILITY_1 = 0.5

# Constants for the 95% confidence interval
CONFIDENCE_LEVEL = 0.95
Z_SCORE = norm.ppf((1 + CONFIDENCE_LEVEL) / 2)  # Z-score for 95% confidence

## Run Simulation with 95% Confidence Interval

In [30]:
# Define the function to run the call center simulation
def simulate_call_center(num_agents, num_calls, seed=42):
    np.random.seed(seed)
    # Generate call arrivals
    arrival_times = np.cumsum(np.random.exponential(scale=1/LAMBDA, size=num_calls))
    # Service times
    service_times = np.random.exponential(scale=MEAN_SERVICE_TIME, size=num_calls)

    # Initialize agents to be ready at time 0
    agents = np.zeros(num_agents)
    wait_times = []
    abandonments = 0

    for i in range(num_calls):
        if arrival_times[i] > SECONDS_OPEN:  # If the call arrives after closing, do not process
            break
        # Check for the first available agent
        available_agent = np.where(agents <= arrival_times[i])[0]
        if available_agent.size > 0:
            agent_index = available_agent[0]
            agents[agent_index] = arrival_times[i] + service_times[i]  # Update agent's next available time
            wait_times.append(0)  # No wait time since the agent is immediately available
        else:
            # All agents are busy, check if any call will be abandoned
            next_available_time = np.min(agents)
            wait_time = next_available_time - arrival_times[i]
            # Generate patience time based on hyperexponential distribution
            patience_time = MAX_PATIENCE_TIME_1 if np.random.rand() < PROBABILITY_1 else MAX_PATIENCE_TIME_2
            if wait_time > patience_time:
                abandonments += 1
            else:
                # Wait for the next agent to be available
                agent_index = np.argmin(agents)
                agents[agent_index] += service_times[i]  # Update agent's next available time
                wait_times.append(wait_time)

    average_wait_time = np.mean(wait_times) if wait_times else 0
    abandonment_rate = abandonments / num_calls

    # Calculate the standard error for both metrics
    se_wait_time = np.std(wait_times) / np.sqrt(len(wait_times)) if wait_times else 0
    se_abandonment_rate = np.sqrt((abandonment_rate * (1 - abandonment_rate)) / num_calls)

    # Calculate the 95% confidence interval for both metrics
    wait_time_ci = (average_wait_time - Z_SCORE * se_wait_time, average_wait_time + Z_SCORE * se_wait_time)
    abandonment_rate_ci = (abandonment_rate - Z_SCORE * se_abandonment_rate, abandonment_rate + Z_SCORE * se_abandonment_rate)

    # Check if the abandonment rate is below the maximum allowed
    if abandonment_rate <= MAX_ABANDONMENT_RATE:
        average_wait_time = np.mean(wait_times) if wait_times else 0
        # Return the simulation results
        return {
            'num_agents': num_agents,
            'average_wait_time': average_wait_time,
            'wait_time_ci': wait_time_ci,
            'abandonment_rate': abandonment_rate,
            'abandonment_rate_ci': abandonment_rate_ci,
            'abandonments': abandonments,
            'total_calls': num_calls,
            'wait_times': wait_times
        }
    else:
        # If the abandonment rate is too high, return None
        return {
            'num_agents': num_agents,
            'average_wait_time': average_wait_time,
            'wait_time_ci': wait_time_ci,
            'abandonment_rate': abandonment_rate,
            'abandonment_rate_ci': abandonment_rate_ci,
            'abandonments': abandonments,
            'total_calls': num_calls,
            'wait_times': []
        }

### Plot Simulation

In [31]:
# Simulate call arrivals
arrival_times = np.cumsum(np.random.exponential(scale=1/LAMBDA, size=int(ARRIVALS_PER_MINUTE * 60 * HOURS_OPEN)))

# Generate patience times based on hyperexponential distribution
patience_times = np.array([
    MAX_PATIENCE_TIME_1 if np.random.rand() < PROBABILITY_1 else MAX_PATIENCE_TIME_2
    for _ in range(len(arrival_times))
])

# Calculate call end times as the sum of arrival times, service times, and patience times
call_end_times = arrival_times + MEAN_SERVICE_TIME + patience_times

# Time points to evaluate the number of calls in progress
time_points = np.arange(0, SECONDS_OPEN + 1, 1)
num_calls_in_progress_b = np.zeros_like(time_points)

# Count the number of calls in progress at each time point
for i, time_point in enumerate(time_points):
    num_calls_in_progress_b[i] = np.sum((arrival_times <= time_point) & (call_end_times > time_point))

# Plotting
fig = go.Figure(data=[
    go.Scatter(x=time_points, y=num_calls_in_progress_b, mode='lines', name='Calls in Progress')
])

# Update the layout
fig.update_layout(
    title="Number of Calls in Progress Over Time",
    xaxis_title="Time (seconds)",
    yaxis_title="Number of Calls in Progress",
    xaxis=dict(range=[0, SECONDS_OPEN]),
    yaxis=dict(range=[0, num_calls_in_progress_b.max() + 1])
)

# Show the figure
fig.show()

## Find the Optimal Staffing 

In [32]:
def find_optimal_staffing():
    num_calls = ARRIVALS_PER_MINUTE * 60 * HOURS_OPEN
    num_agents = int(np.ceil(LAMBDA / MU))  # Start with the theoretical minimum
    optimal_found = False
    results = []

    while not optimal_found:
        simulation_result = simulate_call_center(num_agents, num_calls)
        results.append(simulation_result)

        # Extract metrics and their confidence intervals
        average_wait_time, wait_time_ci = simulation_result['average_wait_time'], simulation_result['wait_time_ci']
        abandonment_rate, abandonment_rate_ci = simulation_result['abandonment_rate'], simulation_result['abandonment_rate_ci']

        # Check if both performance constraints are met within the 95% confidence interval
        if (wait_time_ci[1] <= MAX_WAIT_TIME) and (abandonment_rate_ci[1] <= MAX_ABANDONMENT_RATE):
            optimal_found = True
        else:
            num_agents += 1  # Increase agents if constraints are not met or not within CI

    results_df = pd.DataFrame(results)

    return num_agents, results_df

# Calculate the optimal number of agents needed
simulation_results_with_confidence, simulation_results_df = find_optimal_staffing()

### Optimal Number of Staff

In [33]:
simulation_results_with_confidence

69

### Dataframe with Analysis

In [34]:
simulation_results_df

num_agents  average_wait_time                              wait_time_ci  \
0          60          27.870978    (27.44167689048886, 28.30027949197363)   
1          61          23.900232  (23.478743387709976, 24.321719950303482)   
2          62          19.233659   (18.82288221340443, 19.644436158042065)   
3          63          15.331756  (14.947654082632303, 15.715858064563031)   
4          64          13.438644  (13.071909298995479, 13.805379429187678)   
5          65          10.870057  (10.530466415970047, 11.209646766808852)   
6          66           8.700549     (8.39943489195581, 9.001663849853884)   
7          67           6.668490    (6.401205045494676, 6.935773965512709)   
8          68           5.097173    (4.862201473643933, 5.332144849045274)   
9          69           4.019942    (3.809889698389458, 4.229993438029584)   

   abandonment_rate                             abandonment_rate_ci  \
0          0.042604      (0.03856413956478288, 0.04664419376855045)   
1          0.034583    (0.030928199394611108, 0.038238467272055564)   
2          0.026771     (0.02354196022826302, 0.029999706438403648)   
3          0.019062      (0.01632708596094033, 0.02179791403905967)   
4          0.013229    (0.010943636959511279, 0.015514696373822055)   
5          0.009271   (0.0073537131668678455, 0.011187953499798823)   
6          0.005208   (0.0037684479290122585, 0.006648218737654407)   
7          0.002396   (0.0014178760100631042, 0.003373790656603562)   
8          0.001354   (0.0006185453912192714, 0.002089787942114062)   
9          0.000521  (6.443007824527634e-05, 0.0009772365884213904)   

   abandonments  total_calls  \
0           409         9600   
1           332         9600   
2           257         9600   
3           183         9600   
4           127         9600   
5            89         9600   
6            50         9600   
7            23         9600   
8            13         9600   
9             5         9600   

                                          wait_times  
0                                                 []  
1                                                 []  
2                                                 []  
3  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
4  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
5  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
6  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
7  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
8  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
9  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...

In [35]:
import plotly.graph_objects as go

def plot_simulation_results(simulation_results_df):
    # Initialize figure
    fig = go.Figure()

    # Add a scatter plot for average wait times
    fig.add_trace(go.Scatter(
        x=simulation_results_df['num_agents'], 
        y=simulation_results_df['average_wait_time'], 
        mode='lines+markers', 
        name='Average Wait Time (seconds)'
    ))

    # Add a scatter plot for abandonment rates
    fig.add_trace(go.Scatter(
        x=simulation_results_df['num_agents'], 
        y=simulation_results_df['abandonment_rate'], 
        mode='lines+markers', 
        name='Abandonment Rate',
        yaxis='y2'  # Assign to the secondary y-axis
    ))

    # Edit the layout
    fig.update_layout(
        title='Average Wait Time and Abandonment Rate vs. Number of Agents',
        xaxis_title='Number of Agents',
        yaxis_title='Average Wait Time (seconds)',
        yaxis2=dict(
            title='Abandonment Rate',
            overlaying='y',
            side='right',
            tickformat='.1%'
        ),
        legend=dict(
            x=0.7,
            y=0.95,
            traceorder='reversed',
            title_font_family='Arial',
            font=dict(
                family='Arial',
                size=12,
                color='black'
            ),
            bgcolor='LightSteelBlue',
            bordercolor='Black',
            borderwidth=2
        )
    )

    # Show plot
    fig.show()

# Now you would call this function with the simulation results DataFrame
plot_simulation_results(simulation_results_df)

## Verify that the Average Waiting Time and the Abandonment Rate Match. Use Regenerative Simulation as taught in Class

### Verify Average Waiting Time

#### Simulation 

In [36]:
# Adjusting the simulate_call_center_with_detailed_data function to align with the other functions
def simulate_call_center_with_detailed_data_adjusted(num_agents, num_calls, seed=42):
    np.random.seed(seed)
    arrival_times = np.cumsum(np.random.exponential(scale=1/LAMBDA, size=num_calls))
    service_times = np.random.exponential(scale=MEAN_SERVICE_TIME, size=num_calls)
    agents = np.zeros(num_agents)
    detailed_wait_times = []
    detailed_abandonment_times = []

    for i in range(num_calls):
        if arrival_times[i] > SECONDS_OPEN:
            continue
        available_agent = np.where(agents <= arrival_times[i])[0]
        if available_agent.size > 0:
            agent_index = available_agent[0]
            agents[agent_index] = arrival_times[i] + service_times[i]
            detailed_wait_times.append(0)  # No wait for immediately served calls
        else:
            next_available_time = np.min(agents)
            wait_time = next_available_time - arrival_times[i]
            # Determine patience time
            patience_time = MAX_PATIENCE_TIME_1 if np.random.rand() < PROBABILITY_1 else MAX_PATIENCE_TIME_2
            if wait_time > patience_time:
                detailed_abandonment_times.append(arrival_times[i] + wait_time)
            else:
                agent_index = np.argmin(agents)
                agents[agent_index] = next_available_time + service_times[i]
                detailed_wait_times.append(wait_time)

    return detailed_wait_times, detailed_abandonment_times

# Re-running the simulation with the adjusted function
num_calls = int(ARRIVALS_PER_MINUTE * 60 * HOURS_OPEN)
detailed_wait_times_adjusted, detailed_abandonment_times_adjusted = simulate_call_center_with_detailed_data_adjusted(simulation_results_with_confidence, num_calls)


#### Create Dataframe

In [37]:
# Creating the DataFrame for the adjusted wait times
wait_times_df = pd.DataFrame({'wait_time': detailed_wait_times_adjusted})
wait_times_df['call_number'] = wait_times_df.index + 1


wait_times_df

wait_time  call_number
0      0.000000            1
1      0.000000            2
2      0.000000            3
3      0.000000            4
4      0.000000            5
...         ...          ...
9590   4.081184         9591
9591   8.206937         9592
9592  10.035424         9593
9593  15.220562         9594
9594  14.226098         9595

[9595 rows x 2 columns]

#### Plot Waiting Time (Y-axis) vs No. of Calls (X-axis)

In [38]:
import plotly.express as px

# Plotting the wait times graph similar to the queueing system example
fig = px.line(wait_times_df, x='call_number', y='wait_time',
             labels={'call_number': 'Call Number', 'wait_time': 'Wait Time'},
             title='Wait Times per Call Number')

fig.update_layout(barmode='overlay', bargap=0)
fig.show()

#### Regenrative Simulation Process

In [39]:
# Using the wait_times_df dataframe to identify cycles, cycle lengths, and rewards
# Assuming that a 'cycle' in the context of the call center is a period where wait times are continuously non-zero

# Adding a column to indicate whether the call had a wait time or not
wait_times_df['had_wait'] = wait_times_df['wait_time'] > 0

# Identifying the start of cycles
wait_times_df['cycle_start'] = wait_times_df['had_wait'] & ~wait_times_df['had_wait'].shift(1).fillna(False)

# Assigning cycle numbers
wait_times_df['cycle_number'] = wait_times_df['cycle_start'].cumsum()

# Calculating cycle lengths and rewards
cycle_info = wait_times_df.groupby('cycle_number').agg(
    cycle_length=('call_number', 'count'),  # Count of calls in the cycle
    Reward=('wait_time', 'sum')  # Sum of wait times in the cycle
).reset_index()

cycle_info  # Displaying the first few rows

cycle_number  cycle_length      Reward
0               0           356    0.000000
1               1            21   13.020129
2               2           278    1.576611
3               3            11   31.727078
4               4            10   46.941353
..            ...           ...         ...
150           150            52  784.369219
151           151            38    0.190630
152           152            17    1.190537
153           153           188   69.301851
154           154             6   53.754652

[155 rows x 3 columns]

##### Step 0: Choose the number of cycles (denoted by $ N $) to simulate

In [40]:
N = cycle_info.shape[0]  # The total number of cycles

##### Step 1: Identify regeneration times $ S_0, S_1, \ldots, S_N $ from simulation


##### Step 2: Compute reward for each cycle - Reward in $ n^{th} $ cycle 


##### Step 3: Compute average cycle length, $ \bar{C} = \frac{1}{N} \sum_{n=1}^N C_n $, where $ C_n = S_n - S_{n-1} $ and average reward over cycles, $ \bar{R} = \frac{1}{N} \sum_{n=1}^N R_n $

In [41]:
# Step 3: Compute average cycle length and average reward over cycles
average_cycle_length = cycle_info['cycle_length'].mean()
average_reward = cycle_info['Reward'].mean()

##### Step 4: Output $ \frac{\bar{R}}{\bar{C}} $ as an estimate for as the steady-state average


In [42]:
# Output the average reward over cycles divided by average cycle length
average_reward_per_cycle_length = average_reward / average_cycle_length

##### Step 5: To compute a confidence interval, compute sample variances and covariances as below:

$$ s_{11}^2 = \frac{1}{N - 1} \sum_{i=1}^N (R_i - \bar{R})^2 $$

$$ s_{22}^2 = \frac{1}{N - 1} \sum_{i=1}^N (C_i - \bar{C})^2 $$

$$ s_{12} = \frac{1}{N - 1} \sum_{i=1}^N (R_i - \bar{R})(C_i - \bar{C}) $$

Then take,

$$ s^2 = s_{11}^2 - 2 \frac{\bar{R}}{\bar{C}} s_{12} + \left(\frac{\bar{R}}{\bar{C}}\right)^2 s_{22}^2 $$

In [43]:
# Step 5: Compute sample variances and covariances
s11_squared = ((cycle_info['Reward'] - average_reward) ** 2).sum() / (N - 1)
s22_squared = ((cycle_info['cycle_length'] - average_cycle_length) ** 2).sum() / (N - 1)
s12 = ((cycle_info['Reward'] - average_reward) * (cycle_info['cycle_length'] - average_cycle_length)).sum() / (N - 1)

# The variance of the estimator
s_squared = s11_squared - 2 * (average_reward / average_cycle_length) * s12 + ((average_reward / average_cycle_length) ** 2) * s22_squared

##### Step 6: Output the $ (1 - \alpha) \times 100\% $ as:

$$ \left( \frac{\bar{R}}{\bar{C}} - s\frac{z_{\alpha/2}}{\sqrt{N}}, \frac{\bar{R}}{\bar{C}} + s\frac{z_{\alpha/2}}{\sqrt{N}} \right) $$

In [44]:
# Step 6: Output the 95% confidence interval for the steady-state average
alpha = 0.05  # for a 95% confidence interval
z_alpha_over_2 = t.ppf(1 - alpha/2, df=N-1)  # t-score for 95% CI and N-1 degrees of freedom
margin_of_error = z_alpha_over_2 / (average_cycle_length * (N** 0.5) )

lower_bound = average_reward_per_cycle_length - margin_of_error
upper_bound = average_reward_per_cycle_length + margin_of_error

##### Verify Results

In [45]:
print(average_reward_per_cycle_length)
print(lower_bound)
print(upper_bound)

4.0199415682095205
4.017378292755437
4.022504843663604


### Verify Abandon Rate 

#### Simulation 

In [46]:
# Adjusting the function to align with the earlier functions
def simulate_call_center_with_detailed_data_aligned(num_agents, num_calls, seed=42):
    np.random.seed(seed)
    arrival_times = np.cumsum(np.random.exponential(scale=1/LAMBDA, size=num_calls))
    service_times = np.random.exponential(scale=MEAN_SERVICE_TIME, size=num_calls)
    agents = np.zeros(num_agents)
    detailed_wait_times = []
    detailed_abandonment_times = []

    for i in range(num_calls):
        if arrival_times[i] > SECONDS_OPEN:
            continue
        available_agent = np.where(agents <= arrival_times[i])[0]
        if available_agent.size > 0:
            agent_index = available_agent[0]
            agents[agent_index] = arrival_times[i] + service_times[i]
            detailed_wait_times.append(0)
        else:
            next_available_time = np.min(agents)
            wait_time = next_available_time - arrival_times[i]
            # Determine patience time
            patience_time = MAX_PATIENCE_TIME_1 if np.random.rand() < PROBABILITY_1 else MAX_PATIENCE_TIME_2
            if wait_time > patience_time:
                detailed_abandonment_times.append(arrival_times[i] + wait_time)
            else:
                agent_index = np.argmin(agents)
                agents[agent_index] = next_available_time + service_times[i]
                detailed_wait_times.append(wait_time)

    return detailed_wait_times, detailed_abandonment_times

# Re-running the simulation with adjusted function
optimal_agents_aligned = simulation_results_with_confidence  # Using the optimal value determined earlier
num_calls = int(ARRIVALS_PER_MINUTE * 60 * HOURS_OPEN)
_, detailed_abandonment_times_aligned = simulate_call_center_with_detailed_data_aligned(optimal_agents_aligned, num_calls)


#### Create Dataframe

In [47]:
# Creating the abandonment dataframe
abandonment_df_initial_aligned = pd.DataFrame(np.round(detailed_abandonment_times_aligned), columns=['second'])
abandonment_df_initial_aligned['abandoned_calls'] = 1
abandonment_df_initial_aligned = abandonment_df_initial_aligned.groupby('second').sum().reset_index()

# Creating a complete dataframe with all seconds
all_seconds = np.arange(0, SECONDS_OPEN + 1, 1)
abandonment_df = pd.DataFrame(all_seconds, columns=['second'])
abandonment_df = abandonment_df.merge(abandonment_df_initial_aligned, on='second', how='left')
abandonment_df['abandoned_calls'].fillna(0, inplace=True)

abandonment_df.head()  # Displaying the first few rows

second  abandoned_calls
0       0              0.0
1       1              0.0
2       2              0.0
3       3              0.0
4       4              0.0

#### Plot Abandoned Calls (Y-axis) vs Seconds (X-axis)

In [48]:
# Now we plot the bar graph for abandoned calls per second using Plotly Express
abandonment_fig = px.line(abandonment_df, x='second', y='abandoned_calls',
                         labels={'second': 'Second', 'abandoned_calls': 'Abandoned Calls'},
                         title='Abandoned Calls per Second')


abandonment_fig.show()

#### Regenrative Simulation Process

In [49]:
# Identifying cycles of abandoned calls, similar to wait times analysis
# A 'cycle' in this context will be a period where abandoned calls are continuously non-zero

# Adding a column to indicate whether there was an abandoned call or not
abandonment_df['had_abandonment'] = abandonment_df['abandoned_calls'] > 0

# Identifying the start of cycles
abandonment_df['cycle_start'] = abandonment_df['had_abandonment'] & ~abandonment_df['had_abandonment'].shift(1).fillna(False)

# Assigning cycle numbers
abandonment_df['cycle_number'] = abandonment_df['cycle_start'].cumsum()

# Calculating cycle lengths and rewards (in this case, the reward is the number of abandoned calls)
abandonment_cycle_info = abandonment_df.groupby('cycle_number').agg(
    cycle_length=('second', 'count'),  # Count of seconds in the cycle
    Reward=('abandoned_calls', 'sum')  # Sum of abandoned calls in the cycle
).reset_index()


abandonment_cycle_info

cycle_number  cycle_length  Reward
0             0          7293     0.0
1             1            90     1.0
2             2         16381     3.0
3             3          5037     1.0

##### Step 0: Choose the number of cycles (denoted by $ N $) to simulate

In [50]:
N = cycle_info.shape[0]  # The total number of cycles


##### Step 1: Identify regeneration times $ S_0, S_1, \ldots, S_N $ from simulation

##### Step 2: Compute reward for each cycle - Reward in $ n^{th} $ cycle 

##### Step 3: Compute average cycle length, $ \bar{C} = \frac{1}{N} \sum_{n=1}^N C_n $, where $ C_n = S_n - S_{n-1} $ and average reward over cycles, $ \bar{R} = \frac{1}{N} \sum_{n=1}^N R_n $

In [51]:
# Compute average cycle length and average reward over cycles
average_cycle_length = (abandonment_cycle_info['cycle_length'].mean())
average_cycle_length = (average_cycle_length*9600)/(8*60*60) # TAKE NOTE 
average_reward = abandonment_cycle_info['Reward'].mean()

##### Step 4: Output $ \frac{\bar{R}}{\bar{C}} $ as an estimate for as the steady-state average

In [52]:
# Output the average reward over cycles divided by average cycle length
average_reward_per_cycle_length = average_reward / average_cycle_length

##### Step 5: To compute a confidence interval, compute sample variances and covariances as below:

$$ s_{11}^2 = \frac{1}{N - 1} \sum_{i=1}^N (R_i - \bar{R})^2 $$

$$ s_{22}^2 = \frac{1}{N - 1} \sum_{i=1}^N (C_i - \bar{C})^2 $$

$$ s_{12} = \frac{1}{N - 1} \sum_{i=1}^N (R_i - \bar{R})(C_i - \bar{C}) $$

Then take,

$$ s^2 = s_{11}^2 - 2 \frac{\bar{R}}{\bar{C}} s_{12} + \left(\frac{\bar{R}}{\bar{C}}\right)^2 s_{22}^2 $$

In [53]:
# Compute sample variances and covariances
s11_squared = ((abandonment_cycle_info['Reward'] - average_reward) ** 2).sum() / (N - 1)
s22_squared = ((abandonment_cycle_info['cycle_length'] - average_cycle_length) ** 2).sum() / (N - 1)
s12 = ((abandonment_cycle_info['Reward'] - average_reward) * (abandonment_cycle_info['cycle_length'] - average_cycle_length)).sum() / (N - 1)

# The variance of the estimator
s_squared = s11_squared - 2 * (average_reward / average_cycle_length) * s12 + ((average_reward / average_cycle_length) ** 2) * s22_squared


##### Step 6: Output the $ (1 - \alpha) \times 100\% $ as:

$$ \left( \frac{\bar{R}}{\bar{C}} + \frac{{s}z_{\alpha/2}}{\bar{C}\sqrt{N}}, \frac{\bar{R}}{\bar{C}} - \frac{{s}z_{\alpha/2}}{\bar{C}\sqrt{N}} \right) $$

In [54]:
# Step 6: Output the 95% confidence interval for the steady-state average
alpha = 0.05  # for a 95% confidence interval
z_alpha_over_2 = t.ppf(1 - alpha/2, df=N-1)  # t-score for 95% CI and N-1 degrees of freedom
margin_of_error = z_alpha_over_2 / (average_cycle_length * (N** 0.5) )


lower_bound = average_reward_per_cycle_length - margin_of_error
upper_bound = average_reward_per_cycle_length + margin_of_error


##### Verify Results

In [55]:
print(average_reward_per_cycle_length)
print(lower_bound)
print(upper_bound)

0.0005208152494705045
0.00045470295368703643
0.0005869275452539725


# Part C

Hyperexponential distribution produces the maximum optimal number of agents (69) when compared with uniform distribution (67), since more variability and potential for longer patience periods exist when dealing with hyperexponential distributions.

Under uniform distribution of patience times, each caller would have an equal probability of experiencing one between `MIN_PATIENCE_TIME` and `MAX_PATIENCE_TIME`, thus limiting variance (65.19), making system operation efficient with lower agent count.

On the other hand, hyperexponential distribution combines two exponential distributions with different means (`MAX_PATIENCE_TIME_1` and `MAX_PATIENCE_TIME_2`) but equal probabilty, creating two hyperexponential distributions with equally likely chances for longer patience times (`MAX_PATIENCE_TIME_1` and `MAX_PATIENCE_TIME_2`). This leads to wider ranges in patience times; greater chances for encountering longer waiting times as a result, increasing service times or potentially longer wait times on calls requiring longer service times or potential longer wait times than might otherwise occur under other distribution models.

As a result of the increase of variance (190.11) brought on by hyperexponential distribution, more agents will need to handle potential variations in patience times while providing high levels of service and meeting target performance constraints.